In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
% ls ./dataset

dummy_submission.csv   genome_scores.csv  tags.csv  train.csv
genome_attributes.csv  movies.csv         test.csv


In [2]:
#Loading dataset
df_train_full = pd.read_csv("./dataset/train.csv")
df_test = pd.read_csv("./dataset/test.csv")
df_submission = pd.read_csv("./dataset/dummy_submission.csv")

In [3]:
df_train_full.describe()

userId       movieId        rating
count  5.264336e+06  5.264336e+06  5.264336e+06
mean   4.987450e+03  2.591271e+03  3.360108e+00
std    2.876768e+03  1.996855e+03  1.058213e+00
min    1.000000e+00  0.000000e+00  5.000000e-01
25%    2.501000e+03  1.018000e+03  3.000000e+00
50%    5.012000e+03  2.083000e+03  3.500000e+00
75%    7.472000e+03  3.696000e+03  4.000000e+00
max    9.969000e+03  8.251000e+03  5.000000e+00

In [4]:
#Splitting into test and train data
np.random.seed(5)
indices = np.random.permutation(df_train_full.shape[0])
training_idx, test_idx = indices[:int(0.85*len(df_train_full))], indices[int(0.85*len(df_train_full)):]
df_train, df_csv = df_train_full.iloc[training_idx,:], df_train_full.iloc[test_idx,:]
#Sorting for better data handling and clarity
df_train=df_train.sort_values(by=['userId','movieId']).reset_index(drop=True)
df_csv=df_csv.sort_values(by=['userId','movieId']).reset_index(drop=True)

## <u>Baseline Prediction</u>
We first remove the inheritttent bias between users and movies using a simple baseline prediction.<br>
Here we have three parameters 
miu: 1x1 
bu: users bias 10kx1 [one for each userid]
bi: movie bias 10kx1 [one for each movieid]

In [14]:
#Baseline Prediction


def minibatch(batch_no,df,batch_size):
    '''Generates the batch for mini-batch gradient descent '''
    if (batch_no+1)*batch_size > len(df):
        minibatch_indices = indices[batch_size*(batch_no)::]
    else:        
        minibatch_indices = indices[batch_size*(batch_no):batch_size*(batch_no+1)]
    X_train = df.iloc[minibatch_indices,:]
    X_train = X_train.sort_values(by=['userId','movieId']).reset_index(drop=True)
    return X_train

def loss(parameters,df):
    miu,bu,bi = parameters
    loss = 0
    for i in range(len(df)):
        userid =  df.iloc[i,0]
        movieid = df.iloc[i,1]
        rating = miu+bu[userid]+bi[movieid]
        if rating>5:
            rating = 5
        if rating<0.5:
            rating =0.5
        loss = loss + (df.iloc[i,2]-(miu+bu[userid]+bi[movieid]))**2
    loss = loss/len(df)
    return loss    
        
def Baseline_Training(step_size,lamda,Epochs,batch_size,df):
    '''Does Mini-batch Gradient descent to optimize baseline training error'''
    
    #Initialize values for bu,b'i,miu
    #Since we are given there are 10k users and 10k movie id
    bu = np.zeros(10000)
    bi = np.zeros(10000)
    #Taking initial guess of miu as average of all ratings
    miu = np.mean(df_train.iloc[:,2])
    
    num_batches = df.shape[0]//batch_size + 1
    for epoch in range(Epochs):
        for batch in range(num_batches):
            bui = []
            X = minibatch(batch,df,batch_size)
            for i in range(len(X)):
                userid =  X.iloc[i,0]
                movieid = X.iloc[i,1]
                bui.append((miu+bu[userid]+bi[movieid]))
            #Adding the regularization term
            bu[X.userId.unique()] = (1-step_size*lamda)*bu[X.userId.unique()]
            bi[X.movieId.unique()] = (1-step_size*lamda)*bi[X.movieId.unique()]
            miu = (1-step_size*lamda)*miu            
            for i in range(len(X)):
                userid =  X.iloc[i,0]
                movieid = X.iloc[i,1]            
                bu[userid] = bu[userid] + step_size*(X.iloc[i,2]-bui[i])
                bi[movieid] = bi[movieid] + step_size*(X.iloc[i,2]-bui[i])
                miu = miu + step_size*(X.iloc[i,2]-bui[i])
            print("Epoch:{} Batch:{} ------ Training Error:{}".format(epoch,batch,loss((miu,bu,bi),X)))
    return miu,bu,bi

In [ ]:
np.random.seed(5)
indices = np.random.permutation(df_train.shape[0])

#Hyperparameters
step_size = 0.001
lamda_set = [0,1e-5,1e-3,1e-1,1,10]
Epochs = 12
batch_size = 1024  

loss_cv = 1000
#Regularization parameter tuning
for lamda in lamda_set:
    miu,bu,bi = Baseline_Training(step_size,lamda,Epochs,batch_size,df_train)
    loss_temp = loss((miu,bu,bi),df_csv)
    if loss_temp<loss_cv:
        loss_cv = loss_temp
        Best_lamda = lamda

Epoch:0 Batch:0 ------ Training Error:1.1714682662894842
Epoch:0 Batch:1 ------ Training Error:1.0772382078925489
Epoch:0 Batch:2 ------ Training Error:1.128943907551129
Epoch:0 Batch:3 ------ Training Error:1.1245301310139657
Epoch:0 Batch:4 ------ Training Error:1.144928258097947
Epoch:0 Batch:5 ------ Training Error:1.1669420196000875
Epoch:0 Batch:6 ------ Training Error:1.0366062739375967
Epoch:0 Batch:7 ------ Training Error:1.114409418310391
Epoch:0 Batch:8 ------ Training Error:1.2069447627069727
Epoch:0 Batch:9 ------ Training Error:1.097375325530495
Epoch:0 Batch:10 ------ Training Error:1.1964960687439279
Epoch:0 Batch:11 ------ Training Error:1.058994222149106
Epoch:0 Batch:12 ------ Training Error:1.052256743388909
Epoch:0 Batch:13 ------ Training Error:1.1617518575130608
Epoch:0 Batch:14 ------ Training Error:1.171030615149507
Epoch:0 Batch:15 ------ Training Error:1.1317066328737448
Epoch:0 Batch:16 ------ Training Error:1.0618704765508342
Epoch:0 Batch:17 ------ Trainin

Epoch:0 Batch:142 ------ Training Error:1.0465919262015084
Epoch:0 Batch:143 ------ Training Error:1.0838732843329437
Epoch:0 Batch:144 ------ Training Error:1.1041697716574113
Epoch:0 Batch:145 ------ Training Error:1.1638021274172352
Epoch:0 Batch:146 ------ Training Error:1.0565678530627902
Epoch:0 Batch:147 ------ Training Error:1.074140274377174
Epoch:0 Batch:148 ------ Training Error:1.1332634641677886
Epoch:0 Batch:149 ------ Training Error:1.0922200618455205
Epoch:0 Batch:150 ------ Training Error:1.0886892978086105
Epoch:0 Batch:151 ------ Training Error:1.033706256494282
Epoch:0 Batch:152 ------ Training Error:1.0853577980686877
Epoch:0 Batch:153 ------ Training Error:0.9601984394618152
Epoch:0 Batch:154 ------ Training Error:1.1049967394949636
Epoch:0 Batch:155 ------ Training Error:0.9764465591000411
Epoch:0 Batch:156 ------ Training Error:1.0469996280900393
Epoch:0 Batch:157 ------ Training Error:1.095879906988174
Epoch:0 Batch:158 ------ Training Error:1.1029097462330886


Epoch:0 Batch:283 ------ Training Error:1.060743763538558
Epoch:0 Batch:284 ------ Training Error:1.0417976928205548
Epoch:0 Batch:285 ------ Training Error:1.0936139857557203
Epoch:0 Batch:286 ------ Training Error:1.0604059195884208
Epoch:0 Batch:287 ------ Training Error:1.0124891228562973
Epoch:0 Batch:288 ------ Training Error:1.0067987960290072
Epoch:0 Batch:289 ------ Training Error:1.080422670798217
Epoch:0 Batch:290 ------ Training Error:0.9705028528613058
Epoch:0 Batch:291 ------ Training Error:1.0002488026840997
Epoch:0 Batch:292 ------ Training Error:1.216628430955222
Epoch:0 Batch:293 ------ Training Error:1.027985387987741
Epoch:0 Batch:294 ------ Training Error:1.043894448192298
Epoch:0 Batch:295 ------ Training Error:1.0920132670703915
Epoch:0 Batch:296 ------ Training Error:1.111584591714324
Epoch:0 Batch:297 ------ Training Error:1.074839203739403
Epoch:0 Batch:298 ------ Training Error:1.1294476565654405
Epoch:0 Batch:299 ------ Training Error:1.0674237804134623
Epoc

Epoch:0 Batch:423 ------ Training Error:0.997633628374343
Epoch:0 Batch:424 ------ Training Error:1.034352451633628
Epoch:0 Batch:425 ------ Training Error:0.9803684719420569
Epoch:0 Batch:426 ------ Training Error:1.0168126971885108
Epoch:0 Batch:427 ------ Training Error:0.9938561539755864
Epoch:0 Batch:428 ------ Training Error:1.0292198712132423
Epoch:0 Batch:429 ------ Training Error:1.0648373213482085
Epoch:0 Batch:430 ------ Training Error:1.0488682506618112
Epoch:0 Batch:431 ------ Training Error:1.080703747003863
Epoch:0 Batch:432 ------ Training Error:0.9360252523400444
Epoch:0 Batch:433 ------ Training Error:1.0899305256905385
Epoch:0 Batch:434 ------ Training Error:0.9795597922668823
Epoch:0 Batch:435 ------ Training Error:1.0245770803810732
Epoch:0 Batch:436 ------ Training Error:0.9685277356488435
Epoch:0 Batch:437 ------ Training Error:1.0219460624464412
Epoch:0 Batch:438 ------ Training Error:1.0895147135000438
Epoch:0 Batch:439 ------ Training Error:0.9852562642191167


Epoch:0 Batch:564 ------ Training Error:1.0194384623226924
Epoch:0 Batch:565 ------ Training Error:0.9721386035736661
Epoch:0 Batch:566 ------ Training Error:1.0158716557038368
Epoch:0 Batch:567 ------ Training Error:1.0480553313295198
Epoch:0 Batch:568 ------ Training Error:1.015023344753594
Epoch:0 Batch:569 ------ Training Error:1.0346941202655089
Epoch:0 Batch:570 ------ Training Error:0.9685018806804467
Epoch:0 Batch:571 ------ Training Error:0.9446342632055278
Epoch:0 Batch:572 ------ Training Error:0.9541855412014992
Epoch:0 Batch:573 ------ Training Error:0.9876217079226158
Epoch:0 Batch:574 ------ Training Error:1.0408014162081591
Epoch:0 Batch:575 ------ Training Error:1.0235417839444514
Epoch:0 Batch:576 ------ Training Error:0.9966348849148534
Epoch:0 Batch:577 ------ Training Error:1.0323193172493421
Epoch:0 Batch:578 ------ Training Error:1.003057955476818
Epoch:0 Batch:579 ------ Training Error:1.001282013447238
Epoch:0 Batch:580 ------ Training Error:1.0056864075430296


...

Epoch:0 Batch:2664 ------ Training Error:0.8024750119249737
Epoch:0 Batch:2665 ------ Training Error:0.8100266603021132
Epoch:0 Batch:2666 ------ Training Error:0.853248801903011
Epoch:0 Batch:2667 ------ Training Error:0.8223391220767262
Epoch:0 Batch:2668 ------ Training Error:0.8253715059351583
Epoch:0 Batch:2669 ------ Training Error:0.9130690579665297
Epoch:0 Batch:2670 ------ Training Error:0.8215779413111636
Epoch:0 Batch:2671 ------ Training Error:0.8119400352048326
Epoch:0 Batch:2672 ------ Training Error:0.8175885835169029
Epoch:0 Batch:2673 ------ Training Error:0.9158720518612029
Epoch:0 Batch:2674 ------ Training Error:0.7854649066543132
Epoch:0 Batch:2675 ------ Training Error:0.929421298385689
Epoch:0 Batch:2676 ------ Training Error:0.8273963903569506
Epoch:0 Batch:2677 ------ Training Error:0.8382455582293814
Epoch:0 Batch:2678 ------ Training Error:0.8521617469408908
Epoch:0 Batch:2679 ------ Training Error:0.8487539666258168
Epoch:0 Batch:2680 ------ Training Error:0

Epoch:0 Batch:2801 ------ Training Error:0.8187949738132455
Epoch:0 Batch:2802 ------ Training Error:0.8583186012116735
Epoch:0 Batch:2803 ------ Training Error:0.8221858424338565
Epoch:0 Batch:2804 ------ Training Error:0.8257373729604771
Epoch:0 Batch:2805 ------ Training Error:0.8758606184921698
Epoch:0 Batch:2806 ------ Training Error:0.8484594685289255
Epoch:0 Batch:2807 ------ Training Error:0.826136185439964
Epoch:0 Batch:2808 ------ Training Error:0.863120599799484
Epoch:0 Batch:2809 ------ Training Error:0.8573852590346513
Epoch:0 Batch:2810 ------ Training Error:0.8049217037270221
Epoch:0 Batch:2811 ------ Training Error:0.8329464713419604
Epoch:0 Batch:2812 ------ Training Error:0.8380873828645905
Epoch:0 Batch:2813 ------ Training Error:0.7821018606413775
Epoch:0 Batch:2814 ------ Training Error:0.8342691823420021
Epoch:0 Batch:2815 ------ Training Error:0.7426750695145009
Epoch:0 Batch:2816 ------ Training Error:0.8282120679338744
Epoch:0 Batch:2817 ------ Training Error:0

Epoch:0 Batch:2938 ------ Training Error:0.8395972318961765
Epoch:0 Batch:2939 ------ Training Error:0.8025988411658843
Epoch:0 Batch:2940 ------ Training Error:0.8051099636165834
Epoch:0 Batch:2941 ------ Training Error:0.890000974047069
Epoch:0 Batch:2942 ------ Training Error:0.7931382329078565
Epoch:0 Batch:2943 ------ Training Error:0.831900691620808
Epoch:0 Batch:2944 ------ Training Error:0.804670257209037
Epoch:0 Batch:2945 ------ Training Error:0.815844402779424
Epoch:0 Batch:2946 ------ Training Error:0.838662288242484
Epoch:0 Batch:2947 ------ Training Error:0.8792343842159673
Epoch:0 Batch:2948 ------ Training Error:0.8105751401143229
Epoch:0 Batch:2949 ------ Training Error:0.7951639967500022
Epoch:0 Batch:2950 ------ Training Error:0.7805044131733305
Epoch:0 Batch:2951 ------ Training Error:0.8760222567678434
Epoch:0 Batch:2952 ------ Training Error:0.7537040520077651
Epoch:0 Batch:2953 ------ Training Error:0.8190364715536322
Epoch:0 Batch:2954 ------ Training Error:0.87

Epoch:0 Batch:3075 ------ Training Error:0.7711321010198293
Epoch:0 Batch:3076 ------ Training Error:0.7670087256637063
Epoch:0 Batch:3077 ------ Training Error:0.7787263447985431
Epoch:0 Batch:3078 ------ Training Error:0.8012662709197967
Epoch:0 Batch:3079 ------ Training Error:0.8758885759519243
Epoch:0 Batch:3080 ------ Training Error:0.854625235449151
Epoch:0 Batch:3081 ------ Training Error:0.8492195415664455
Epoch:0 Batch:3082 ------ Training Error:0.8182446053978136
Epoch:0 Batch:3083 ------ Training Error:0.8461791814205708
Epoch:0 Batch:3084 ------ Training Error:0.7789361085865154
Epoch:0 Batch:3085 ------ Training Error:0.7673770117665742
Epoch:0 Batch:3086 ------ Training Error:0.8954974274358419
Epoch:0 Batch:3087 ------ Training Error:0.8460630515286813
Epoch:0 Batch:3088 ------ Training Error:0.7772861682011803
Epoch:0 Batch:3089 ------ Training Error:0.8353966587807403
Epoch:0 Batch:3090 ------ Training Error:0.8340496444991919
Epoch:0 Batch:3091 ------ Training Error:

Epoch:0 Batch:3212 ------ Training Error:0.8433249981660733
Epoch:0 Batch:3213 ------ Training Error:0.7736361887664513
Epoch:0 Batch:3214 ------ Training Error:0.8025767982518472
Epoch:0 Batch:3215 ------ Training Error:0.8123331267427855
Epoch:0 Batch:3216 ------ Training Error:0.7793115687277139
Epoch:0 Batch:3217 ------ Training Error:0.8483611655093201
Epoch:0 Batch:3218 ------ Training Error:0.8617082886022226
Epoch:0 Batch:3219 ------ Training Error:0.7932301882114079
Epoch:0 Batch:3220 ------ Training Error:0.7630793265759269
Epoch:0 Batch:3221 ------ Training Error:0.8437843204992672
Epoch:0 Batch:3222 ------ Training Error:0.7959359460332979
Epoch:0 Batch:3223 ------ Training Error:0.7633257078086799
Epoch:0 Batch:3224 ------ Training Error:0.8772487914412564
Epoch:0 Batch:3225 ------ Training Error:0.8357116615761059
Epoch:0 Batch:3226 ------ Training Error:0.8323509179466985
Epoch:0 Batch:3227 ------ Training Error:0.7821965162946714
Epoch:0 Batch:3228 ------ Training Error

In [ ]:
print('Final Training Loss:{} \n Final Test set loss:{}'.format(loss((miu,bu,bi),df_train),loss((miu,bu,bi),df_csv)))

In [209]:
#Submission
predictions = np.zeros(len(df_test))
for i in range(len(df_test)):
    userid =  df_test.iloc[i,0]
    movieid = df_test.iloc[i,1]
    rating = float("{0:.1f}".format(miu+bu[userid]+bi[movieid]))
    if rating>5:
        rating = 5
    if rating<0.5:
        rating =0.5
    predictions[i] = rating
df_submission.Prediction = predictions
df_submission.to_csv('./Submission.csv',index=False)